# Dask DataFrames

In this notebook we demonstrate how to work with dask dataframes. 

* A few words about dask dataframes
* Weather station data
* Tuning read_csv
* Compute using dask.dataframe
* Write to Parquet for a better performance
* Read Parquet to compare
* More calculation for exercise
* Dask.dataframe vs. Pandas

-----


- Authors: NCI Virtual Research Environment Team
- Keywords: Dask, Dataframe, csv
- Create Date: 2020-May
- Lineage/Reference: This tutorial is referenced to [dask tutorial](https://github.com/dask/dask-tutorial).

----

### Prerequisite

The following modules are needed:

* Pandas
* Dask
* Pyarrow


## Dask DataFrames

We built a parallel dataframe computation over a directory of CSV files using `dask.delayed` in the example of using Paleoceanography data. In this section we use `dask.dataframe` to automatically build similiar computations, for the common case of tabular computations. Dask dataframes look and feel like Pandas dataframes but they run on the same infrastructure that powers `dask.delayed`.

#### Dask DataFrame Data Model

So far, the biggest difference we've seen is that Dask operations are lazy; they build up a task graph instead of executing immediately.
This lets Dask do operations in parallel and out of core.

In the Dask array example, we saw that a `dask.array` was composed of many NumPy arrays, chunked along one or more dimensions. It's similar for `dask.dataframe`: a Dask DataFrame is composed of many pandas DataFrames. For `dask.dataframe` the chunking happens only along the index.

<img src="http://dask.pydata.org/en/latest/_images/dask-dataframe.svg" width="30%">

We call each chunk a *partition*, and the upper / lower bounds are *divisions*.
Dask *can* store information about the divisions. You can operate on dataframe per partition at a time when you write custom functions to apply to Dask DataFrames.

The `dask.dataframe` module implements a blocked parallel `DataFrame` object that mimics a large subset of the Pandas `DataFrame`. One Dask `DataFrame` is comprised of many in-memory pandas `DataFrames` separated along the index. One operation on a Dask `DataFrame` triggers many pandas operations on the constituent pandas `DataFrame`s in a way that is mindful of potential parallelism and memory constraints.

**Main Take-aways**

1.  Dask DataFrame should be familiar to Pandas users
2.  The partitioning of dataframes is important for efficient execution

#### When to use `dask.dataframe`

In this notebook we use the weather stations within 50km of Acton, ACT. The data can be downloaded from [the Australian Bureau of Meterology climate data service site](http://www.bom.gov.au/climate/data/stations/). But now rather than write for-loops we let `dask.dataframe` construct our computations.  The `dask.dataframe.read_csv` function can take a globstring like `"data/weather_stations_ACT/*.csv"` and build parallel computations on all of our data at once.

Pandas is great for tabular datasets that fit in memory. Dask becomes useful when the dataset you want to analyze is larger than your machine's RAM. The demo dataset we're working with is only about 65MB, so that you can download it in a reasonable time, but `dask.dataframe` will scale to datasets much larger than memory.

### Weather station data

In [3]:
import os
import dask
filename = os.path.join('data', 'weather_stations_ACT','IDCJAC0009_*_*','IDCJAC0009*.csv')
filename

'data/weather_stations_ACT/IDCJAC0009_*_*/IDCJAC0009*.csv'

Filename includes a glob pattern `*`, so all files in the path matching that pattern will be read into the same Dask DataFrame.

We can read one file with `pandas.read_csv` or many files with `dask.dataframe.read_csv`

In [4]:
import pandas as pd
df = pd.read_csv('data/weather_stations_ACT/IDCJAC0009_042010_2015/IDCJAC0009_042010_2015_Data.csv')
df.head()

Product code  Bureau of Meteorology station number  Year  Month  Day  \
0   IDCJAC0009                                 42010  2015      1    1   
1   IDCJAC0009                                 42010  2015      1    2   
2   IDCJAC0009                                 42010  2015      1    3   
3   IDCJAC0009                                 42010  2015      1    4   
4   IDCJAC0009                                 42010  2015      1    5   

   Rainfall amount (millimetres)  \
0                            0.0   
1                           20.0   
2                           15.2   
3                            0.0   
4                            0.0   

   Period over which rainfall was measured (days) Quality  
0                                             NaN       Y  
1                                             1.0       Y  
2                                             1.0       Y  
3                                             NaN       Y  
4                                             NaN       Y

In [9]:
import dask.dataframe as dd
dd = dd.read_csv(filename)
dd

Dask DataFrame Structure:
                Product code Bureau of Meteorology station number   Year  Month    Day Rainfall amount (millimetres) Period over which rainfall was measured (days) Quality
npartitions=125                                                                                                                                                            
                      object                                int64  int64  int64  int64                       float64                                        float64  object
                         ...                                  ...    ...    ...    ...                           ...                                            ...     ...
...                      ...                                  ...    ...    ...    ...                           ...                                            ...     ...
                         ...                                  ...    ...    ...    ...                           ...                                            ...     ...
                         ...                                  ...    ...    ...    ...                           ...                                            ...     ...
Dask Name: from-delayed, 375 tasks

Notice that the respresentation of the dataframe object contains no data - Dask has just done enough to read the start of the first file, and infer the column names and dtypes.

Also data dataframe uses "from-delayed" so that 375 tasks are read efficiently into the memory. 

We can view the start and end of the data

In [4]:
dd.head()

Product code  Bureau of Meteorology station number  Year  Month  Day  \
0   IDCJAC0009                                 42010  2015      1    1   
1   IDCJAC0009                                 42010  2015      1    2   
2   IDCJAC0009                                 42010  2015      1    3   
3   IDCJAC0009                                 42010  2015      1    4   
4   IDCJAC0009                                 42010  2015      1    5   

   Rainfall amount (millimetres)  \
0                            0.0   
1                           20.0   
2                           15.2   
3                            0.0   
4                            0.0   

   Period over which rainfall was measured (days) Quality  
0                                             NaN       Y  
1                                             1.0       Y  
2                                             1.0       Y  
3                                             NaN       Y  
4                                             NaN       Y

In [5]:
dd.tail()  # this fails

Product code  Bureau of Meteorology station number  Year  Month  Day  \
1395   IDCJAC0009                                 73148  2007     10   27   
1396   IDCJAC0009                                 73148  2007     10   28   
1397   IDCJAC0009                                 73148  2007     10   29   
1398   IDCJAC0009                                 73148  2007     10   30   
1399   IDCJAC0009                                 73148  2007     10   31   

      Rainfall amount (millimetres)  \
1395                           12.5   
1396                            1.0   
1397                           10.4   
1398                            0.0   
1399                            0.0   

      Period over which rainfall was measured (days) Quality  
1395                                             3.0       Y  
1396                                             1.0       Y  
1397                                             1.0       Y  
1398                                             NaN       Y  
1399                                             NaN       Y

In [6]:
# load and count number of rows
len(dd)

1754661

What happened here?
- Dask investigated the input path and found all 125 matching files (see **npartitions=125**)
- a set of jobs was intelligently created for each chunk - one per original CSV file in this case
- each file was loaded into a pandas dataframe, had `len()` applied to it
- the subtotals were combined to give you the final grand total.

### Tuning read_csv

The Pandas `read_csv` function has many options to help you parse files. The Dask version uses the Pandas function internally, and so supports many of the same options. You can use the `?` operator to see the full documentation string.

In [6]:
pd.read_csv?

Signature:
pd.read_csv(
    filepath_or_buffer: Union[str, pathlib.Path, IO[~AnyStr]],
    sep=',',
    delimiter=None,
    header='infer',
    names=None,
    index_col=None,
    usecols=None,
    squeeze=False,
    prefix=None,
    mangle_dupe_cols=True,
    dtype=None,
    engine=None,
    converters=None,
    true_values=None,
    false_values=None,
    skipinitialspace=False,
    skiprows=None,
    skipfooter=0,
    nrows=None,
    na_values=None,
    keep_default_na=True,
    na_filter=True,
    verbose=False,
    skip_blank_lines=True,
    parse_dates=False,
    infer_datetime_format=False,
    keep_date_col=False,
    date_parser=None,
    dayfirst=False,
    cache_dates=True,
    iterator=False,
    chunksize=None,
    compression='infer',
    thousands=None,
    decimal: str = '.',
    lineterminator=None,
    quotechar='"',
    quoting=0,
    doublequote=True,
    escapechar=None,
    comment=None,
    encoding=None,
    dialect=None,
    error_bad_lines=True,
    warn_bad_l

In this case we use the `parse_dates` keyword to parse the timestamp column to be a datetime. This will make things more efficient in the future. Notice that the dtype of the timestamp column has changed from `object` to `datetime64[ns]`.

Unlike `pandas.read_csv` which reads in the entire file before inferring datatypes, `dask.dataframe.read_csv` only reads in a sample from the beginning of the file (or first file if using a glob). These inferred datatypes are then enforced when reading all partitions.

In this case, the datatypes inferred in the sample are incorrect. The `Bureau of Meteorology station number` should be strings (`object` dtype), rather than integer.  Note that Dask gives an informative error message about the mismatch. We can fix this by directly specify the `dtypes` of the offending columns. 

## Computations with `dask.dataframe`

We compute the maximum of the `Rainfall amount (millimetres)` column. With just pandas, we would loop over each file to find the individual maximums, then find the final maximum over all the individual maximums

```python
from glob import glob

maxes = []
filenames = sorted(glob('data/weather_stations_ACT/IDCJAC0009_*_*/IDCJAC0009*.csv'))
for fn in filenames:
    df = pd.read_csv(fn)
    # rename column names to shorter strings
    df.columns = ['code','station','year','month','day','rainfall','period','quality']
    maxes.append(df.rainfall.max())
    
final_max = max(maxes)
```

We could wrap that `pd.read_csv` with `dask.delayed` so that it runs in parallel. Regardless, we're still having to think about loops, intermediate results (one per file) and the final reduction (`max` of the intermediate maxes). This is just noise around the real task, which pandas solves with

```python
df.rainfall.max()
```

`dask.dataframe` lets us write pandas-like code, that operates on larger than memory datasets in parallel.

**Compare the runtime of the following two blocks of code:**

In [11]:
%%time

from glob import glob

maxes = []
filenames = sorted(glob('data/weather_stations_ACT/IDCJAC0009_*_*/IDCJAC0009*.csv'))
for fn in filenames:
    df = pd.read_csv(fn)
    # rename column names to shorter strings
    df.columns = ['code','station','year','month','day','rainfall','period','quality']
    maxes.append(df.rainfall.max())
    
final_max = max(maxes)

CPU times: user 1.95 s, sys: 258 ms, total: 2.21 s
Wall time: 5.88 s


In [12]:
dd.columns = ['code','station','year','month','day','rainfall','period','quality']
%time dd.rainfall.max().compute()

CPU times: user 3.86 s, sys: 739 ms, total: 4.6 s
Wall time: 2.53 s


322.1

This writes the delayed computation for us and then runs it.  

Some things to note:

1.  As with `dask.delayed`, we need to call `.compute()` when we're done.  Up until this point everything is lazy.
2.  Dask will delete intermediate results (like the full pandas dataframe for each file) as soon as possible.
    -  This lets us handle datasets that are larger than memory
    -  This means that repeated computations will have to load all of the data in each time (run the code above again, is it faster or slower than you would expect?)
    
As with `Delayed` objects, you can view the underlying task graph using the `.visualize` method:

In [13]:
# notice the parallelism
dd.rainfall.max().visualize()

dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.964104 to fit


### Write to Parquet

Whenever we operate on our dataframe we read through all of our CSV data so that we don’t fill up RAM. This is very efficient for memory use, but reading through all of the CSV files every time can be slow.

Instead, we’ll store our data in Parquet, a format that is more efficient for computers to read and write. It is binary file format. Parquet stores nested data structures in a flat columnar format. Compared to a traditional approach where data is stored in row-oriented approach, parquet is more efficient in terms of storage and performance.

In [16]:
dd.to_parquet('data/ACT_weather.parquet', engine='pyarrow')

In [17]:
!ls data/ACT_weather.parquet 

_common_metadata  part.13.parquet  part.42.parquet  part.71.parquet
_metadata	  part.14.parquet  part.43.parquet  part.72.parquet
part.0.parquet	  part.15.parquet  part.44.parquet  part.73.parquet
part.1.parquet	  part.16.parquet  part.45.parquet  part.74.parquet
part.10.parquet   part.17.parquet  part.46.parquet  part.75.parquet
part.100.parquet  part.18.parquet  part.47.parquet  part.76.parquet
part.101.parquet  part.19.parquet  part.48.parquet  part.77.parquet
part.102.parquet  part.2.parquet   part.49.parquet  part.78.parquet
part.103.parquet  part.20.parquet  part.5.parquet   part.79.parquet
part.104.parquet  part.21.parquet  part.50.parquet  part.8.parquet
part.105.parquet  part.22.parquet  part.51.parquet  part.80.parquet
part.106.parquet  part.23.parquet  part.52.parquet  part.81.parquet
part.107.parquet  part.24.parquet  part.53.parquet  part.82.parquet
part.108.parquet  part.25.parquet  part.54.parquet  part.83.parquet
part.109.parquet  part.26.parquet  part.55.parquet  part.

### Read from Parquet

In [18]:
%%time 
new_df = pd.read_parquet('data/ACT_weather.parquet', engine='pyarrow')
new_df.rainfall.max()

CPU times: user 933 ms, sys: 217 ms, total: 1.15 s
Wall time: 1.31 s


322.1

#### Select only the columns that you plan to use

Parquet is a column-store, which means that it can efficiently pull out only a few columns from your dataset. This is good because it helps to avoid unnecessary data loading.

In [19]:
%%time
new_df = pd.read_parquet('data/ACT_weather.parquet', columns=['rainfall'], engine='pyarrow')
new_df.rainfall.max()

CPU times: user 554 ms, sys: 91.6 ms, total: 645 ms
Wall time: 947 ms


322.1

## Exercises

In this section we do a few `dask.dataframe` computations. If you are comfortable with Pandas then these should be familiar. You will have to think about when to call `compute`.

### 1.) How many rows are in our dataset?

If you aren't familiar with pandas, how would you check how many records are in a list of tuples?

In [98]:
len(dd)

1754661

### 2.) In total, how many days records were taken?

*Hint*: `count()` counts non-NaN values.

In [20]:
period = pd.read_parquet('data/ACT_weather.parquet', columns=['period'], engine='pyarrow')
period.count()

period    418018
dtype: int64

### 3.) In total, how many non-record days from each weather station?

*Hint*: use [`df.groupby`](https://pandas.pydata.org/pandas-docs/stable/groupby.html).

In [21]:
dd.groupby("station").period.count().compute()

station
42010       41
70000    10222
70011    11574
70014     8377
70015     6168
         ...  
70354     1010
71073     4099
72011     2606
72157      377
73148      243
Name: period, Length: 125, dtype: int64

### 4.) What was the average rainfall from each station?

In [22]:
dd.groupby("station").rainfall.mean().compute()

station
42010    1.372022
70000    1.767808
70011    1.760142
70014    1.689061
70015    1.791328
           ...   
70354    1.790016
71073    2.526155
72011    2.510485
72157    2.541190
73148    1.709147
Name: rainfall, Length: 125, dtype: float64

## Sharing Intermediate Results

When computing all of the above, we sometimes did the same operation more than once. For most operations, `dask.dataframe` hashes the arguments, allowing duplicate computations to be shared, and only computed once.

For example, lets compute the mean and standard deviation for all station rainfall. Since dask operations are lazy, those values aren't the final results yet. They're just the recipe required to get the result.

If we compute them with two calls to compute, there is no sharing of intermediate computations.

In [23]:
%%time
mean_rainfall = dd.groupby("station").period.count().mean().compute()
std_rainfall = dd.groupby("station").period.count().std().compute()

CPU times: user 8.99 s, sys: 1.7 s, total: 10.7 s
Wall time: 6.15 s


But lets try by passing both to a single `compute` call.

In [24]:
%%time

mean_rainfall, std_rainfall = dask.compute(dd.groupby("station").period.count().mean(), dd.groupby("station").period.count().std())

CPU times: user 4.54 s, sys: 778 ms, total: 5.31 s
Wall time: 3.05 s


Using `dask.compute` takes roughly 1/2 the time. This is because the task graphs for both results are merged when calling `dask.compute`, allowing shared operations to only be done once instead of twice. In particular, using `dask.compute` only does the following once:

- the calls to dataframe object
- groupby each station
- get the non-value of periods

To see what the merged task graphs between multiple results look like (and what's shared), you can use the `dask.visualize` function (we might want to use `filename='graph.pdf'` to zoom in on the graph better):

In [27]:
dask.visualize(mean_rainfall, std_rainfall)

### Close the client

Before moving on to the next exercise, make sure to close your client or stop this kernel.

In [ ]:
client.close()

## How does this compare to Pandas?

Pandas is more mature and fully featured than `dask.dataframe`.  If your data fits in memory then you should use Pandas.  The `dask.dataframe` module gives you a limited `pandas` experience when you operate on datasets that don't fit comfortably in memory.

During this tutorial we provide a small dataset consisting of a few CSV files.  This dataset is 65MB on disk, small enough that you would normally use Pandas.

We've chosen this size so that exercises finish quickly.  Dask.dataframe only really becomes meaningful for problems significantly larger than this, when Pandas breaks with the dreaded 

    MemoryError:  ...
    
Furthermore, the distributed scheduler allows the same dataframe expressions to be executed across a cluster. To enable massive "big data" processing, one could execute data ingestion functions such as `read_csv`, where the data is held on storage accessible to every worker node, and because most operations begin by selecting only some columns, transforming and filtering the data, only relatively small amounts of data need to be communicated between the machines.

Dask.dataframe operations use `pandas` operations internally.  Generally they run at about the same speed except in the following two cases:

1.  Dask introduces a bit of overhead, around 1ms per task.  This is usually negligible.
2.  When Pandas releases the GIL (coming to `groupby` in the next version) `dask.dataframe` can call several pandas operations in parallel within a process, increasing speed somewhat proportional to the number of cores. For operations which don't release the GIL, multiple processes would be needed to get the same speedup.

## Limitations

### What doesn't work?

Dask.dataframe only covers a small but well-used portion of the Pandas API.
This limitation is for two reasons:

1.  The Pandas API is *huge*
2.  Some operations are genuinely hard to do in parallel (e.g. sort)

Additionally, some important operations like ``set_index`` work, but are slower
than in Pandas because they include substantial shuffling of data, and may write out to disk.

## Learn More


* [DataFrame documentation](https://docs.dask.org/en/latest/dataframe.html)
* [DataFrame screencast](https://youtu.be/AT2XtFehFSQ)
* [DataFrame API](https://docs.dask.org/en/latest/dataframe-api.html)
* [DataFrame examples](https://examples.dask.org/dataframe.html)
* [Pandas documentation](https://pandas.pydata.org/pandas-docs/stable/)